
#            Capstone Project - The Battle of the Neighborhoods (Week 2)



# 

### Applied Data Science Capstone by IBM/Coursera¶


## Introduction: Business Problem 

In this project we will try to find an optimal location for a Shopping Mall. Specifically, this report will be targeted to stakeholders interested in opening an **Shopping mall** in **Toronto, Canada**.

Since there are lots of Shopping malls in Toronto city, we will try to detect locations that are not already placed with Shopping mall. We are also particularly interested in areas with no Shopping mall. We would also prefer locations as close to city center as possible, assuming that first two conditions are met.

We will use our data science powers to generate a few most promissing neighborhoods based on this criteria. Advantages of each area will then be clearly expressed so that best possible final location can be chosen by stakeholders.

## Data 

Based on definition of our problem, factors that will influence our decission are:
* number of existing malls in the neighborhood (any mall)
* number of and distance to malls in the neighborhood, if any
* distance of neighborhood from city center

We decided to use regularly spaced grid of locations, centered around city center, to define our neighborhoods.

Following data sources will be needed to extract/generate the required information:
* number of restaurants and their type and location in every neighborhood will be obtained using **Foursquare API**
* coordinate of Toronto city will be obtained using **the Wikipedia data**

## Neighborhood Candidates

Let's create latitude & longitude coordinates for centroids of our candidate neighborhoods. 

Let's first find the latitude & longitude of Toronto, using specific, well known address and  Reading and Explore Dataset from wikipedia

In [1]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option("display.max_columns", None)
pd.set_option("display.max_rows", None)

import json # library to handle JSON files

!pip install geopy
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values
import requests # library to handle requests
!pip install geocoder
import geocoder

from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

import folium # map rendering library

print("Libraries imported.")

Libraries imported.


## Scrap data from Wikipedia page into a DataFrame¶


In [2]:
toronto = pd.read_html("https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M")
tor_df = toronto[0]

# define the dataframe columns
tor_df.columns = ['PostalCode', 'Borough', 'Neighborhood']
tor_df = tor_df.loc[:]

# Extracting and cleaning the data
tor_df = tor_df[tor_df.Borough != 'Not assigned']
tor_df = tor_df.groupby(['PostalCode','Borough'], as_index=False).agg(lambda x: ','.join(x))

tor_df

PostalCode           Borough  \
0          M1B       Scarborough   
1          M1C       Scarborough   
2          M1E       Scarborough   
3          M1G       Scarborough   
4          M1H       Scarborough   
5          M1J       Scarborough   
6          M1K       Scarborough   
7          M1L       Scarborough   
8          M1M       Scarborough   
9          M1N       Scarborough   
10         M1P       Scarborough   
11         M1R       Scarborough   
12         M1S       Scarborough   
13         M1T       Scarborough   
14         M1V       Scarborough   
15         M1W       Scarborough   
16         M1X       Scarborough   
17         M2H        North York   
18         M2J        North York   
19         M2K        North York   
20         M2L        North York   
21         M2M        North York   
22         M2N        North York   
23         M2P        North York   
24         M2R        North York   
25         M3A        North York   
26         M3B        North York   
27         M3C        North York   
28         M3H        North York   
29         M3J        North York   
30         M3K        North York   
31         M3L        North York   
32         M3M        North York   
33         M3N        North York   
34         M4A        North York   
35         M4B         East York   
36         M4C         East York   
37         M4E      East Toronto   
38         M4G         East York   
39         M4H         East York   
40         M4J         East York   
41         M4K      East Toronto   
42         M4L      East Toronto   
43         M4M      East Toronto   
44         M4N   Central Toronto   
45         M4P   Central Toronto   
46         M4R   Central Toronto   
47         M4S   Central Toronto   
48         M4T   Central Toronto   
49         M4V   Central Toronto   
50         M4W  Downtown Toronto   
51         M4X  Downtown Toronto   
52         M4Y  Downtown Toronto   
53         M5A  Downtown Toronto   
54         M5B  Downtown Toronto   
55         M5C  Downtown Toronto   
56         M5E  Downtown Toronto   
57         M5G  Downtown Toronto   
58         M5H  Downtown Toronto   
59         M5J  Downtown Toronto   
60         M5K  Downtown Toronto   
61         M5L  Downtown Toronto   
62         M5M        North York   
63         M5N   Central Toronto   
64         M5P   Central Toronto   
65         M5R   Central Toronto   
66         M5S  Downtown Toronto   
67         M5T  Downtown Toronto   
68         M5V  Downtown Toronto   
69         M5W  Downtown Toronto   
70         M5X  Downtown Toronto   
71         M6A        North York   
72         M6B        North York   
73         M6C              York   
74         M6E              York   
75         M6G  Downtown Toronto   
76         M6H      West Toronto   
77         M6J      West Toronto   
78         M6K      West Toronto   
79         M6L        North York   
80         M6M              York   
81         M6N              York   
82         M6P      West Toronto   
83         M6R      West Toronto   
84         M6S      West Toronto   
85         M7A  Downtown Toronto   
86         M7R       Mississauga   
87         M7Y      East Toronto   
88         M8V         Etobicoke   
89         M8W         Etobicoke   
90         M8X         Etobicoke   
91         M8Y         Etobicoke   
92         M8Z         Etobicoke   
93         M9A         Etobicoke   
94         M9B         Etobicoke   
95         M9C         Etobicoke   
96         M9L        North York   
97         M9M        North York   
98         M9N              York   
99         M9P         Etobicoke   
100        M9R         Etobicoke   
101        M9V         Etobicoke   
102        M9W         Etobicoke   

                                          Neighborhood  
0                                       Malvern, Rouge  
1               Rouge Hill, Port Union, Highland Creek  
2                    Guildwood, Morningside, West Hill  
3                              

In [3]:
# create a new DataFrame
tor = pd.DataFrame(tor_df["Neighborhood"])

tor.head()

Neighborhood
0                          Malvern, Rouge
1  Rouge Hill, Port Union, Highland Creek
2       Guildwood, Morningside, West Hill
3                                  Woburn
4                               Cedarbrae

In [4]:
tor.shape

(103, 1)

In [5]:
# define a function to get coordinates
def get_latlng(neighborhood):
    # initialize your variable to None
    lat_lng_coords = None
    # loop until you get the coordinates
    while(lat_lng_coords is None):
        g = geocoder.arcgis('{}, Toronto, Canada'.format(neighborhood))
        lat_lng_coords = g.latlng
    return lat_lng_coords

In [6]:
# call the function to get the coordinates, store in a new list using list comprehension
coords = [ get_latlng(neighborhood) for neighborhood in tor["Neighborhood"].tolist() ]

## Get the geographical coordinates.

In [7]:
coords

[[43.81023000000005, -79.22037999999998],
 [43.789480000000026, -79.17613999999998],
 [43.766032820796575, -79.18538886171193],
 [43.767480000000035, -79.22828999999996],
 [43.747740961533395, -79.23517827086341],
 [43.738650000000064, -79.21698999999995],
 [43.71357596734874, -79.26034393370531],
 [43.72751000000005, -79.28274999999996],
 [43.738650000000064, -79.21698999999995],
 [43.694720000000075, -79.26459999999997],
 [43.737040000000036, -79.27693999999997],
 [43.74860000000007, -79.29801999999995],
 [43.78626000000003, -79.28083999999996],
 [43.78643000000005, -79.30155999999994],
 [43.809300000000064, -79.26706999999999],
 [43.79861815260895, -79.30883671057614],
 [43.80927938589406, -79.18769371605126],
 [43.803030000000035, -79.35345999999998],
 [43.772290000000055, -79.34085999999996],
 [43.777100000000075, -79.37956999999994],
 [43.75763000000006, -79.37118999999996],
 [43.79036719630047, -79.410854302354],
 [43.77094195854672, -79.40260722961315],
 [43.744158943504665, -7

In [8]:
# create temporary dataframe to populate the coordinates into Latitude and Longitude
df_coords = pd.DataFrame(coords, columns=['Latitude', 'Longitude'])

# merge the coordinates into the original dataframe
tor['Latitude'] = df_coords['Latitude']
tor['Longitude'] = df_coords['Longitude']


In [9]:
tor

Neighborhood   Latitude   Longitude
0                                       Malvern, Rouge  43.810230  -79.220380
1               Rouge Hill, Port Union, Highland Creek  43.789480  -79.176140
2                    Guildwood, Morningside, West Hill  43.766033  -79.185389
3                                               Woburn  43.767480  -79.228290
4                                            Cedarbrae  43.747741  -79.235178
5                                  Scarborough Village  43.738650  -79.216990
6          Kennedy Park, Ionview, East Birchmount Park  43.713576  -79.260344
7                      Golden Mile, Clairlea, Oakridge  43.727510  -79.282750
8      Cliffside, Cliffcrest, Scarborough Village West  43.738650  -79.216990
9                          Birch Cliff, Cliffside West  43.694720  -79.264600
10   Dorset Park, Wexford Heights, Scarborough Town...  43.737040  -79.276940
11                                   Wexford, Maryvale  43.748600  -79.298020
12                                           Agincourt  43.786260  -79.280840
13             Clarks Corners, Tam O'Shanter, Sullivan  43.786430  -79.301560
14   Milliken, Agincourt North, Steeles East, L'Amo...  43.809300  -79.267070
15                       Steeles West, L'Amoreaux West  43.798618  -79.308837
16                                         Upper Rouge  43.809279  -79.187694
17                                   Hillcrest Village  43.803030  -79.353460
18                        Fairview, Henry Farm, Oriole  43.772290  -79.340860
19                                     Bayview Village  43.777100  -79.379570
20                            York Mills, Silver Hills  43.757630  -79.371190
21                             Willowdale, Newtonbrook  43.790367  -79.410854
22                         Willowdale, Willowdale East  43.770942  -79.402607
23                                     York Mills West  43.744159  -79.402843
24                         Willowdale, Willowdale West  43.771340  -79.428020
25                                           Parkwoods  43.686588  -79.409996
26                                           Don Mills  43.705685  -79.333857
27                                           Don Mills  43.705685  -79.333857
28     Bathurst Manor, Wilson Heights, Downsview North  43.737370  -79.434170
29                     Northwood Park, York University  43.742650  -79.496470
30                                           Downsview  43.720197  -79.499895
31                                           Downsview  43.720197  -79.499895
32                                           Downsview  43.720197  -79.499895
33                                           Downsview  43.720197  -79.499895
34                                    Victoria Village  43.731540  -79.314280
35                     Parkview Hill, Woodbine Gardens  43.706260  -79.300910
36                                    Woodbine Heights  43.687520  -79.320590
37                                         The Beaches  43.674130  -79.296440
38                                             Leaside  43.700237  -79.351065
39                                    Thorncliffe Park  43.707320  -79.343530
40       East Toronto, Broadview North (Old East York)  43.689370  -79.354290
41                        The Danforth West, Riverdale  43.690670  -79.290792
42                      India Bazaar, The Beaches West  43.674130  -79.296440
43                                     Studio District  48.929710    1.790410
44                                       Lawrence Park  43.725540  -79.402320
45                                    Davisville North  43.700634  -79.385359
46                   North Toronto West, Lawrence Park  43.724000  -79.401980
47                                          Davisville  43.701750  -79.383520
48                         Moore Park, Summerhill East  43.611853  -79.488754
49   Summerhill West, Rathnelly, South Hill, Forest...  43.694310  -79.416100
50                                            Rosedale  43.67707

In [10]:
tor.shape

(103, 3)

In [11]:
# save the DataFrame as CSV file
tor.to_csv("Toronto_data.csv", index=False)
print("saved !")

saved !


##  Create a map of Kuala Lumpur with neighborhoods superimposed on top

In [12]:
#Let's get the geographical coordinates of Toronto.

address = 'Toronto, Canada'

geolocator = Nominatim(user_agent="toronto_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Toronto are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Toronto are 43.6534817, -79.3839347.


In [13]:
# create map of Toronto using latitude and longitude values

map_toronto = folium.Map(location=[latitude, longitude], zoom_start=10)

for lat, lng, neighborhood in zip(tor['Latitude'], tor['Longitude'], tor['Neighborhood']):
    label = '{}'.format(neighborhood,)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_toronto)  
    
map_toronto

In [14]:
# save the map as HTML file
map_toronto.save('map_toronto.html')

## Use the Foursquare API to explore the neighborhoods¶


In [15]:
#### Define Foursquare Credentials and Version

CLIENT_ID = 'NTGPC5RJAON11PWDMVPGKU2OFEOMORGX13ZRM1UWFFOEEFUL' # your Foursquare ID
CLIENT_SECRET = 'JAEFH4YYHKMRKRZ14UHCKICYGZB5EUWWIMRHDBYRDNFIZWYO' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version
print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: NTGPC5RJAON11PWDMVPGKU2OFEOMORGX13ZRM1UWFFOEEFUL
CLIENT_SECRET:JAEFH4YYHKMRKRZ14UHCKICYGZB5EUWWIMRHDBYRDNFIZWYO


Now, let's get the top 100 venues that are in Toronto within a radius of 2000 meters.

In [17]:
radius = 1000
LIMIT = 100

venues = []

for lat, long, neighborhood in zip(tor['Latitude'], tor['Longitude'], tor['Neighborhood']):
    
    # create the API request URL
    url = "https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}".format(
        CLIENT_ID,
        CLIENT_SECRET,
        VERSION,
        lat,
        long,
        radius, 
        LIMIT)
    
    # make the GET request
    results = requests.get(url).json()["response"]['groups'][0]['items']
    
    # return only relevant information for each nearby venue
    for venue in results:
        venues.append((
            neighborhood,
            lat, 
            long, 
            venue['venue']['name'], 
            venue['venue']['location']['lat'], 
            venue['venue']['location']['lng'],  
            venue['venue']['categories'][0]['name']))


In [18]:
# convert the venues list into a new DataFrame
toronto_venues = pd.DataFrame(venues)

# define the column names
toronto_venues.columns = ['Neighborhood', 'Latitude', 'Longitude', 'VenueName', 'VenueLatitude', 'VenueLongitude', 'VenueCategory']

print(toronto_venues.shape)
toronto_venues

(5183, 7)


Neighborhood   Latitude  \
0                                        Malvern, Rouge  43.810230   
1                                        Malvern, Rouge  43.810230   
2                                        Malvern, Rouge  43.810230   
3                                        Malvern, Rouge  43.810230   
4                                        Malvern, Rouge  43.810230   
5                                        Malvern, Rouge  43.810230   
6                                        Malvern, Rouge  43.810230   
7                                        Malvern, Rouge  43.810230   
8                                        Malvern, Rouge  43.810230   
9                                        Malvern, Rouge  43.810230   
10                                       Malvern, Rouge  43.810230   
11                                       Malvern, Rouge  43.810230   
12                                       Malvern, Rouge  43.810230   
13                                       Malvern, Rouge  43.810230   
14                                       Malvern, Rouge  43.810230   
15                                       Malvern, Rouge  43.810230   
16               Rouge Hill, Port Union, Highland Creek  43.789480   
17               Rouge Hill, Port Union, Highland Creek  43.789480   
18               Rouge Hill, Port Union, Highland Creek  43.789480   
19               Rouge Hill, Port Union, Highland Creek  43.789480   
20               Rouge Hill, Port Union, Highland Creek  43.789480   
21               Rouge Hill, Port Union, Highland Creek  43.789480   
22                    Guildwood, Morningside, West Hill  43.766033   
23                    Guildwood, Morningside, West Hill  43.766033   
24                    Guildwood, Morningside, West Hill  43.766033   
25                    Guildwood, Morningside, West Hill  43.766033   
26                    Guildwood, Morningside, West Hill  43.766033   
27                    Guildwood, Morningside, West Hill  43.766033   
28                    Guildwood, Morningside, West Hill  43.766033   
29                    Guildwood, Morningside, West Hill  43.766033   
30                    Guildwood, Morningside, West Hill  43.766033   
31                    Guildwood, Morningside, West Hill  43.766033   
32                    Guildwood, Morningside, West Hill  43.766033   
33                    Guildwood, Morningside, West Hill  43.766033   
34                    Guildwood, Morningside, West Hill  43.766033   
35                    Guildwood, Morningside, West Hill  43.766033   
36                    Guildwood, Morningside, West Hill  43.766033   
37                    Guildwood, Morningside, West Hill  43.766033   
38                    Guildwood, Morningside, West Hill  43.766033   
39                    Guildwood, Morningside, West Hill  43.766033   
40                    Guildwood, Morningside, West Hill  43.766033   
41                    Guildwood, Morningside, West Hill  43.766033   
42                    Guildwood, Morningside, West Hill  43.766033   
43                    Guildwood, Morningside, West Hill  43.766033   
44                    Guildwood, Morningside, West Hill  43.766033   
45                    Guildwood, Morningside, West Hill  43.766033   
46                    Guildwood, Morningside, West Hill  43.766033   
47                    Guildwood, Morningside, West Hill  43.766033   
48                    Guildwood, Morningside, West Hill  43.766033   
49                    Guildwood, Morningside, West Hill  43.766033   
50                    Guildwood, Morningside, West Hill  43.766033   
51                    Guildwood, Morningside, West Hill  43.766033   
52                    Guildwood, Morningside, West Hill  43.766033   
53                    Guildwood, Morningside, West Hill  43.766033   
54                    Guildwood, Morningside, West Hill  43.766033   
55                    Guildwood, Morningside, West Hill  43.766033   
56                    Guildwood, Morningside, West Hi

#### Let's check how many venues were returned for each neighorhood



In [19]:
toronto_venues.groupby('Neighborhood').count()

Latitude  Longitude  \
Neighborhood                                                              
Agincourt                                                 40         40   
Alderwood, Long Branch                                    29         29   
Bathurst Manor, Wilson Heights, Downsview North           26         26   
Bayview Village                                           28         28   
Bedford Park, Lawrence Manor East                         13         13   
Berczy Park                                              100        100   
Birch Cliff, Cliffside West                               15         15   
Brockton, Parkdale Village, Exhibition Place             100        100   
Business reply mail Processing Centre, South Ce...       100        100   
CN Tower, King and Spadina, Railway Lands, Harb...       100        100   
Caledonia-Fairbanks                                       27         27   
Canada Post Gateway Processing Centre                    100        100   
Cedarbrae                                                  7          7   
Central Bay Street                                        79         79   
Christie                                                  60         60   
Church and Wellesley                                     100        100   
Clarks Corners, Tam O'Shanter, Sullivan                   36         36   
Cliffside, Cliffcrest, Scarborough Village West           22         22   
Commerce Court, Victoria Hotel                           100        100   
Davisville                                                85         85   
Davisville North                                          94         94   
Del Ray, Mount Dennis, Keelsdale and Silverthorn          25         25   
Don Mills                                                 76         76   
Dorset Park, Wexford Heights, Scarborough Town ...        18         18   
Downsview                                                 80         80   
Dufferin, Dovercourt Village                             100        100   
East Toronto, Broadview North (Old East York)             31         31   
Eringate, Bloordale Gardens, Old Burnhamthorpe,...        20         20   
Fairview, Henry Farm, Oriole                              79         79   
First Canadian Place, Underground city                   100        100   
Garden District, Ryerson                                 100        100   
Glencairn                                                 38         38   
Golden Mile, Clairlea, Oakridge                           87         87   
Guildwood, Morningside, West Hill                         40         40   
Harbourfront East, Union Station, Toronto Islands         30         30   
High Park, The Junction South                             79         79   
Hillcrest Village                                         24         24   
Humber Summit                                              6          6   
Humberlea, Emery                                           9          9   
Humewood-Cedarvale                                        56         56   
India Bazaar, The Beaches West                            88         88   
Islington Avenue, Humber Valley Village                   14         14   
Kennedy Park, Ionview, East Birchmount Park                9          9   
Kensington Market, Chinatown, Grange Park                100        100   
Kingsview Village, St. Phillips, Martin Grove G...        21         21   
Lawrence Manor, Lawrence Heights                          36         36   
Lawrence Park                                             53         53   
Leaside                                                   44         44   
Little Portugal, Trinity                                 100        100   
Malvern, Rouge                                            16         16   
Milliken, Agincourt North, Steeles East, L'Amor...        27         27   
Mimico NW, The Queensway West, South of Bloor, ...       100        100   
Mo

In [20]:
print('There are {} uniques categories.'.format(len(toronto_venues['VenueCategory'].unique())))

There are 318 uniques categories.


In [21]:
# print out the list of categories
toronto_venues['VenueCategory'].unique()[:50]

array(['Pharmacy', 'Sandwich Place', 'Fast Food Restaurant',
       'Skating Rink', 'Pizza Place', 'Grocery Store', 'Bubble Tea Shop',
       'Supermarket', 'Park', 'Salon / Barbershop', 'Neighborhood',
       'Italian Restaurant', 'Breakfast Spot', 'Burger Joint',
       'Fish & Chips Shop', 'Gym', 'Fried Chicken Joint',
       'Food & Drink Shop', 'Liquor Store', 'Smoothie Shop',
       'Coffee Shop', 'Restaurant', 'Bank', 'Beer Store', 'Sports Bar',
       'Greek Restaurant', 'Discount Store', 'Laundromat', 'Intersection',
       'Bus Station', 'Mexican Restaurant', 'Thrift / Vintage Store',
       'Medical Center', 'Chinese Restaurant', 'Automotive Shop',
       'Gym / Fitness Center', 'Convenience Store', 'Spa',
       'Asian Restaurant', 'Home Service', 'Indian Restaurant',
       'Music Store', 'Paper / Office Supplies Store',
       'Vietnamese Restaurant', 'Taco Place', 'Electronics Store',
       'Ice Cream Shop', 'Butcher', 'Big Box Store', 'Seafood Restaurant'],
      dtype

## Analyzeing Each Neighborhood

In [22]:
# one hot encoding
toronto_onehot = pd.get_dummies(toronto_venues[['VenueCategory']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
toronto_onehot['Neighborhood'] = toronto_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [toronto_onehot.columns[-1]] + list(toronto_onehot.columns[:-1])
toronto_onehot = toronto_onehot[fixed_columns]


print(toronto_onehot.shape)
toronto_onehot.head()

(5183, 318)


Zoo Exhibit  Accessories Store  Afghan Restaurant  African Restaurant  \
0            0                  0                  0                   0   
1            0                  0                  0                   0   
2            0                  0                  0                   0   
3            0                  0                  0                   0   
4            0                  0                  0                   0   

   American Restaurant  Animal Shelter  Antique Shop  Aquarium  Arcade  \
0                    0               0             0         0       0   
1                    0               0             0         0       0   
2                    0               0             0         0       0   
3                    0               0             0         0       0   
4                    0               0             0         0       0   

   Argentinian Restaurant  Art Gallery  Art Museum  Arts & Crafts Store  \
0                       0            0           0                    0   
1                       0            0           0                    0   
2                       0            0           0                    0   
3                       0            0           0                    0   
4                       0            0           0                    0   

   Asian Restaurant  Athletics & Sports  Australian Restaurant  \
0                 0                   0                      0   
1                 0                   0                      0   
2                 0                   0                      0   
3                 0                   0                      0   
4                 0                   0                      0   

   Auto Dealership  Auto Garage  Automotive Shop  BBQ Joint  Baby Store  \
0                0            0                0          0           0   
1                0            0                0          0           0   
2                0            0                0          0           0   
3                0            0                0          0           0   
4                0            0                0          0           0   

   Bagel Shop  Bakery  Bank  Bar  Baseball Field  Baseball Stadium  \
0           0       0     0    0               0                 0   
1           0       0     0    0               0                 0   
2           0       0     0    0               0                 0   
3           0       0     0    0               0                 0   
4           0       0     0    0               0                 0   

   Basketball Stadium  Beach  Beach Bar  Beer Bar  Beer Store  \
0                   0      0          0         0           0   
1                   0      0          0         0           0   
2                   0      0          0         0           0   
3                   0      0          0         0           0   
4                   0      0          0         0           0   

   Belgian Restaurant  Big Box Store  Bike Rental / Bike Share  Bike Shop  \
0                   0              0                         0          0   
1                   0              0                         0          0   
2                   0              0                         0          0   
3                   0              0                         0          0   
4                   0              0                         0          0   

   Bistro  Bookstore  Botanical Garden  Boutique  Bowling Alley  \
0       0          0                 0         0              0   
1       0          0                 0         0              0   
2       0          0                 0         0              0   
3       0          0                 0         0              0   
4       0          0                 0         0              0   

   Brazilian Restaurant  Breakfast Spot  Brewery  Bridal Shop  Bridge  \
0                     0               0        0   

#### Next, let's group rows by neighborhood and by taking the mean of the frequency of occurrence of each category



In [23]:
toronto_grouped = toronto_onehot.groupby('Neighborhood').mean().reset_index()
toronto_grouped

Neighborhood  Zoo Exhibit  \
0                                           Agincourt     0.000000   
1                              Alderwood, Long Branch     0.000000   
2     Bathurst Manor, Wilson Heights, Downsview North     0.000000   
3                                     Bayview Village     0.000000   
4                   Bedford Park, Lawrence Manor East     0.000000   
5                                         Berczy Park     0.000000   
6                         Birch Cliff, Cliffside West     0.000000   
7        Brockton, Parkdale Village, Exhibition Place     0.000000   
8   Business reply mail Processing Centre, South C...     0.000000   
9   CN Tower, King and Spadina, Railway Lands, Har...     0.000000   
10                                Caledonia-Fairbanks     0.000000   
11              Canada Post Gateway Processing Centre     0.000000   
12                                          Cedarbrae     0.000000   
13                                 Central Bay Street     0.000000   
14                                           Christie     0.000000   
15                               Church and Wellesley     0.000000   
16            Clarks Corners, Tam O'Shanter, Sullivan     0.000000   
17    Cliffside, Cliffcrest, Scarborough Village West     0.000000   
18                     Commerce Court, Victoria Hotel     0.000000   
19                                         Davisville     0.000000   
20                                   Davisville North     0.000000   
21   Del Ray, Mount Dennis, Keelsdale and Silverthorn     0.000000   
22                                          Don Mills     0.000000   
23  Dorset Park, Wexford Heights, Scarborough Town...     0.000000   
24                                          Downsview     0.000000   
25                       Dufferin, Dovercourt Village     0.000000   
26      East Toronto, Broadview North (Old East York)     0.000000   
27  Eringate, Bloordale Gardens, Old Burnhamthorpe...     0.000000   
28                       Fairview, Henry Farm, Oriole     0.000000   
29             First Canadian Place, Underground city     0.000000   
30                           Garden District, Ryerson     0.000000   
31                                          Glencairn     0.000000   
32                    Golden Mile, Clairlea, Oakridge     0.000000   
33                  Guildwood, Morningside, West Hill     0.000000   
34  Harbourfront East, Union Station, Toronto Islands     0.000000   
35                      High Park, The Junction South     0.000000   
36                                  Hillcrest Village     0.000000   
37                                      Humber Summit     0.000000   
38                                   Humberlea, Emery     0.000000   
39                                 Humewood-Cedarvale     0.000000   
40                     India Bazaar, The Beaches West     0.000000   
41            Islington Avenue, Humber Valley Village     0.000000   
42        Kennedy Park, Ionview, East Birchmount Park     0.000000   
43          Kensington Market, Chinatown, Grange Park     0.000000   
44  Kingsview Village, St. Phillips, Martin Grove ...     0.000000   
45                   Lawrence Manor, Lawrence Heights     0.000000   
46                                      Lawrence Park     0.000000   
47                                            Leaside     0.000000   
48                           Little Portugal, Trinity     0.000000   
49                                     Malvern, Rouge     0.000000   
50  Milliken, Agincourt North, Steeles East, L'Amo...     0.000000   
51  Mimico NW, The Queensway West, South of Bloor,...     0.000000   
52                        Moore Park, Summerhill East     0.000000   
53       New Toronto, Mimico South, Humber Bay Shores     0.000000   
54           North Park, Maple Leaf Park, Upwood Park     0.000000   
55                  North Toronto West, Lawrence Park     0.000000   
56                Northwest, West Humber - Clairvil

In [24]:
toronto_grouped.shape


(98, 318)

In [25]:
len(toronto_grouped[toronto_grouped["Shopping Mall"] > 0])


22

#### Create a new DataFrame for Shopping Mall data only




In [26]:
toronto_mall = toronto_grouped[["Neighborhood","Shopping Mall"]]


In [27]:
toronto_mall.head()


Neighborhood  Shopping Mall
0                                        Agincourt          0.025
1                           Alderwood, Long Branch          0.000
2  Bathurst Manor, Wilson Heights, Downsview North          0.000
3                                  Bayview Village          0.000
4                Bedford Park, Lawrence Manor East          0.000

## Cluster Neighborhoods

In [28]:
kclusters = 3

toronto_mall_clustering = toronto_mall.drop('Neighborhood', 1)


kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(toronto_mall_clustering)


kmeans.labels_[0:10]


array([1, 0, 0, 0, 0, 0, 0, 0, 0, 0], dtype=int32)

In [29]:
# create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.
toronto_merged = toronto_mall.copy()

# add clustering labels
toronto_merged["Cluster Labels"] = kmeans.labels_
toronto_merged.rename(columns={"Neighborhoods": "Neighborhood"}, inplace=True)
toronto_merged.head()

Neighborhood  Shopping Mall  \
0                                        Agincourt          0.025   
1                           Alderwood, Long Branch          0.000   
2  Bathurst Manor, Wilson Heights, Downsview North          0.000   
3                                  Bayview Village          0.000   
4                Bedford Park, Lawrence Manor East          0.000   

   Cluster Labels  
0               1  
1               0  
2               0  
3               0  
4               0

In [30]:
# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
toronto_merged = toronto_merged.join(tor.set_index("Neighborhood"), on="Neighborhood")

print(toronto_merged.shape)
toronto_merged.head() # check the last columns!

(102, 5)


Neighborhood  Shopping Mall  \
0                                        Agincourt          0.025   
1                           Alderwood, Long Branch          0.000   
2  Bathurst Manor, Wilson Heights, Downsview North          0.000   
3                                  Bayview Village          0.000   
4                Bedford Park, Lawrence Manor East          0.000   

   Cluster Labels   Latitude  Longitude  
0               1  43.786260 -79.280840  
1               0  43.593540 -79.532750  
2               0  43.737370 -79.434170  
3               0  43.777100 -79.379570  
4               0  43.779584 -79.136784

In [31]:
# sort the results by Cluster Labels
print(toronto_merged.shape)
toronto_merged.sort_values(["Cluster Labels"], inplace=True)
toronto_merged

(102, 5)


Neighborhood  Shopping Mall  \
46                                      Lawrence Park       0.000000   
68                                 Runnymede, Swansea       0.000000   
67             Rouge Hill, Port Union, Highland Creek       0.000000   
66                                           Roselawn       0.000000   
65                                           Rosedale       0.010000   
64                           Richmond, Adelaide, King       0.000000   
63                          Regent Park, Harbourfront       0.000000   
62        Queen's Park, Ontario Provincial Government       0.011236   
61                                          Parkwoods       0.000000   
60                    Parkview Hill, Woodbine Gardens       0.000000   
59                             Parkdale, Roncesvalles       0.000000   
58  Old Mill South, King's Mill Park, Sunnylea, Hu...       0.000000   
57                    Northwood Park, York University       0.000000   
56                Northwest, West Humber - Clairville       0.000000   
55                  North Toronto West, Lawrence Park       0.000000   
54           North Park, Maple Leaf Park, Upwood Park       0.000000   
53       New Toronto, Mimico South, Humber Bay Shores       0.000000   
52                        Moore Park, Summerhill East       0.000000   
51  Mimico NW, The Queensway West, South of Bloor,...       0.000000   
50  Milliken, Agincourt North, Steeles East, L'Amo...       0.000000   
49                                     Malvern, Rouge       0.000000   
48                           Little Portugal, Trinity       0.000000   
69                      Runnymede, The Junction North       0.000000   
96                                    York Mills West       0.000000   
70                                Scarborough Village       0.000000   
72                                     St. James Town       0.000000   
95                                   Woodbine Heights       0.000000   
94                                             Woburn       0.000000   
93                        Willowdale, Willowdale West       0.000000   
92                        Willowdale, Willowdale East       0.012658   
90                                  Wexford, Maryvale       0.000000   
89                                             Weston       0.000000   
88                                          Westmount       0.000000   
87  West Deane Park, Princess Gardens, Martin Grov...       0.000000   
86                                   Victoria Village       0.000000   
85                                        Upper Rouge       0.000000   
84                     University of Toronto, Harbord       0.000000   
83           Toronto Dominion Centre, Design Exchange       0.000000   
82                                   Thorncliffe Park       0.000000   
81      The Kingsway, Montgomery Road, Old Mill North       0.000000   
80                       The Danforth West, Riverdale       0.000000   
79                                        The Beaches       0.011364   
78                The Annex, North Midtown, Yorkville       0.010000   
77  Summerhill West, Rathnelly, South Hill, Forest...       0.000000   
76                                    Studio District       0.000000   
75                                     Stn A PO Boxes       0.000000   
73                        St. James Town, Cabbagetown       0.000000   
71  South Steeles, Silverstone, Humbergate, Jamest...       0.000000   
45                   Lawrence Manor, Lawrence Heights       0.000000   
97                           York Mills, Silver Hills       0.000000   
43          Kensington Market, Chinatown, Grange Park       0.000000   
22                                          Don Mills       0.000000   
20                                   Davisville North       0.000000   
19                                         Davisville       0.000000   
18                     Commerce Court, Victoria Hotel       0.010000   
17    Cli

Finally, let's visualize the resulting clusters


In [32]:
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)


x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]


markers_colors = []
for lat, lon, poi, cluster in zip(toronto_merged['Latitude'], toronto_merged['Longitude'], toronto_merged['Neighborhood'], toronto_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

In [33]:
# save the map as HTML file
map_clusters.save('map_clusters.html')
print('saved')

saved


## Examine Clusters

#### Cluster 1

In [39]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 0]                                               
                                                        

Neighborhood  Shopping Mall  \
46                                      Lawrence Park       0.000000   
68                                 Runnymede, Swansea       0.000000   
67             Rouge Hill, Port Union, Highland Creek       0.000000   
66                                           Roselawn       0.000000   
65                                           Rosedale       0.010000   
64                           Richmond, Adelaide, King       0.000000   
63                          Regent Park, Harbourfront       0.000000   
62        Queen's Park, Ontario Provincial Government       0.011236   
61                                          Parkwoods       0.000000   
60                    Parkview Hill, Woodbine Gardens       0.000000   
59                             Parkdale, Roncesvalles       0.000000   
58  Old Mill South, King's Mill Park, Sunnylea, Hu...       0.000000   
57                    Northwood Park, York University       0.000000   
56                Northwest, West Humber - Clairville       0.000000   
55                  North Toronto West, Lawrence Park       0.000000   
54           North Park, Maple Leaf Park, Upwood Park       0.000000   
53       New Toronto, Mimico South, Humber Bay Shores       0.000000   
52                        Moore Park, Summerhill East       0.000000   
51  Mimico NW, The Queensway West, South of Bloor,...       0.000000   
50  Milliken, Agincourt North, Steeles East, L'Amo...       0.000000   
49                                     Malvern, Rouge       0.000000   
48                           Little Portugal, Trinity       0.000000   
69                      Runnymede, The Junction North       0.000000   
96                                    York Mills West       0.000000   
70                                Scarborough Village       0.000000   
72                                     St. James Town       0.000000   
95                                   Woodbine Heights       0.000000   
94                                             Woburn       0.000000   
93                        Willowdale, Willowdale West       0.000000   
92                        Willowdale, Willowdale East       0.012658   
90                                  Wexford, Maryvale       0.000000   
89                                             Weston       0.000000   
88                                          Westmount       0.000000   
87  West Deane Park, Princess Gardens, Martin Grov...       0.000000   
86                                   Victoria Village       0.000000   
85                                        Upper Rouge       0.000000   
84                     University of Toronto, Harbord       0.000000   
83           Toronto Dominion Centre, Design Exchange       0.000000   
82                                   Thorncliffe Park       0.000000   
81      The Kingsway, Montgomery Road, Old Mill North       0.000000   
80                       The Danforth West, Riverdale       0.000000   
79                                        The Beaches       0.011364   
78                The Annex, North Midtown, Yorkville       0.010000   
77  Summerhill West, Rathnelly, South Hill, Forest...       0.000000   
76                                    Studio District       0.000000   
75                                     Stn A PO Boxes       0.000000   
73                        St. James Town, Cabbagetown       0.000000   
71  South Steeles, Silverstone, Humbergate, Jamest...       0.000000   
45                   Lawrence Manor, Lawrence Heights       0.000000   
97                           York Mills, Silver Hills       0.000000   
43          Kensington Market, Chinatown, Grange Park       0.000000   
22                                          Don Mills       0.000000   
20                                   Davisville North       0.000000   
19                                         Davisville       0.000000   
18                     Commerce Court, Victoria Hotel       0.010000   
17    Cli

#### Cluster 2

In [40]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 1]

Neighborhood  Shopping Mall  \
47                                            Leaside       0.022727   
91                            Willowdale, Newtonbrook       0.023810   
74                      Steeles West, L'Amoreaux West       0.029412   
36                                  Hillcrest Village       0.041667   
10                                Caledonia-Fairbanks       0.037037   
34  Harbourfront East, Union Station, Toronto Islands       0.033333   
21   Del Ray, Mount Dennis, Keelsdale and Silverthorn       0.040000   
0                                           Agincourt       0.025000   

    Cluster Labels   Latitude  Longitude  
47               1  43.700237 -79.351065  
91               1  43.790367 -79.410854  
74               1  43.798618 -79.308837  
36               1  43.803030 -79.353460  
10               1  43.688570 -79.454830  
34               1  43.798899 -79.146156  
21               1  43.684040 -79.464550  
0                1  43.786260 -79.280840

#### Cluster 3

In [41]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 2]

Neighborhood  Shopping Mall  \
41            Islington Avenue, Humber Valley Village       0.071429   
44  Kingsview Village, St. Phillips, Martin Grove ...       0.095238   

    Cluster Labels  Latitude  Longitude  
41               2  43.66328 -79.531537  
44               2  43.68339 -79.557040

### Observations:

Most of the shopping malls are concentrated in the central area of Totonot city, with the highest number in cluster 2 and moderate number in cluster 3. On the other hand, cluster 1 has very low number to totally no shopping mall in the neighborhoods. This represents a great opportunity and high potential areas to open new shopping malls as there is very little to no competition from existing malls. Meanwhile, shopping malls in cluster 2 are likely suffering from intense competition due to oversupply and high concentration of shopping malls. From another perspective, this also shows that the oversupply of shopping malls mostly happened in the central area of the city, with the area still have very few shopping malls. Therefore, this project recommends property developers to capitalize on these findings to open new shopping malls in neighborhoods in cluster 1 with little to no competition. Property developers with unique selling propositions to stand out from the competition can also open new shopping malls in neighborhoods in cluster 3 with less competition. Lastly, property developers are advised to avoid neighborhoods in cluster 2 which already have high concentration of shopping malls and suffering from intense competition.

## Thank You!!!!!!
